### Uploading usefull libraries

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import time
import json
import tpqoa
api = tpqoa.tpqoa("oanda.cfg")

## Creating class for price action strategy

In [2]:
class breakout_swing():
    ''' Class for analyzing failed swings.

    Attributes
    ==========
    ticker: str
        ticker symbol with which to work with
    tf: str
        granularity of data i.e: D, H1, M5
    reward: int
        reward to risk ration given in number
    spread: int
        spread on the ticker used to calculate costs of trading

    Methods
    =======
    check_strategy:
        iterative backtesting method to create df with entered trades
    check_outcome:
        adjusts the trades: droping ones not closed and duplicated entries
    '''
    def __init__(self, reward, spread):
        self.reward = reward
        self.spread = spread
    
    #Add more information about class
    def __repr__(self):
        return "breakout_swing(Reward = {}/1, spread = {})".format(self.reward,self.spread)
    
    def check_strategy(self):
        ''' Iterative backtester through uploaded data
        '''
        # Create empty df to save all trades made
        self.trades = pd.DataFrame(columns = ['time','position','entry_price','sl','tp','outcome_pips','total_amount_fixed'])
        self.trades.set_index('time', inplace=True)
        self.df = data.copy(deep=True)
        
        start_time = time.time()
        for bar in range(len(self.df)):
            # Trading only between 7 and 17
            if self.df.hour.iloc[bar] >= 7 and self.df.hour.iloc[bar] <= 17:
                # If both indicators are equal -1 then sell the asset
                if self.df.dhs2.iloc[bar] == -1 and self.df.dls2.iloc[bar] == -1:
                    if self.df.l.iloc[bar] < self.df.lows.iloc[bar-1] and self.df.o.iloc[bar] > self.df.lows.iloc[bar-1]:
                        trade = pd.DataFrame([[self.df.index[bar], #time bar
                                               'short', #long position
                                               round(self.df.lows.iloc[bar-1] - self.spread, 6), #entry price
                                               round(self.df.highs.iloc[bar-1] + self.spread, 6), #stop loss price
                                               round(self.df.lows.iloc[bar-1] - (self.reward * (self.df.highs.iloc[bar-1] + self.spread - (self.df.lows.iloc[bar-1] - self.spread)) - self.spread), 6), # take profit price
                                               0,0]], # the rest of columns will be filled once trade is closed
                                     columns = ['time','position','entry_price','sl','tp','outcome_pips','total_amount_fixed'])
                        trade.set_index('time', inplace=True)
                        self.trades = self.trades.append(trade)
                        print("{}: BS_fixed | Go Short | Price: {} | SL: {} | TP: {}".format(self.df.index[bar].date(), self.trades.entry_price[-1], self.trades.sl[-1], self.trades.tp[-1]))
                    
                # If both indicators are equal 1 then buy the asset
                elif self.df.dls2.iloc[bar] == 1 and self.df.dhs2.iloc[bar] == 1:
                    if self.df.h.iloc[bar] > self.df.highs.iloc[bar-1] and self.df.o.iloc[bar] < self.df.highs.iloc[bar-1]:
                        trade = pd.DataFrame([[self.df.index[bar], #time bar
                                               'long', #long position
                                               round(self.df.highs.iloc[bar-1] + self.spread, 6), #entry price
                                               round(self.df.lows.iloc[bar-1] - self.spread, 6), #stop loss price
                                               round(self.df.highs.iloc[bar-1] + (self.reward * (self.df.highs.iloc[bar-1] + self.spread - (self.df.lows.iloc[bar-1] - self.spread)) + self.spread), 6), # take profit price
                                               0,0]], # the rest of columns will be filled once trade is closed
                                     columns = ['time','position','entry_price','sl','tp','outcome_pips','total_amount_fixed'])
                        trade.set_index('time', inplace=True)
                        self.trades = self.trades.append(trade)
                        print("{}: BS_fixed | Go Long  | Price: {} | SL: {} | TP: {}".format(self.df.index[bar].date(), self.trades.entry_price[-1], self.trades.sl[-1], self.trades.tp[-1]))
            
            # Check if already open trades do not require to be closed:
            for t in range(len(self.trades)):
                # Check long positions:
                if self.trades.outcome_pips.iloc[t] == 0 and self.trades.index[t].date() < self.df.index[bar].date() and self.trades.position.iloc[t] == 'long':
                    if self.df.l.iloc[bar] < self.trades.sl.iloc[t]:
                        self.trades.outcome_pips.iloc[t] = -(self.trades.entry_price.iloc[t] - self.trades.sl.iloc[t])
                        print("{}: Long Position from {} closed | SL: {}".format(self.df.index[bar].date(), self.trades.index[t].date(), self.trades.sl.iloc[t]))
                    elif self.df.h.iloc[bar] > self.trades.tp.iloc[t]:
                        self.trades.outcome_pips.iloc[t] = self.trades.tp.iloc[t] - self.trades.entry_price.iloc[t]
                        print("{}: Long Position from {} closed | TP: {}".format(self.df.index[bar].date(), self.trades.index[t].date(), self.trades.tp.iloc[t]))
                
                # Check short positions:
                elif self.trades.outcome_pips.iloc[t] == 0 and self.trades.index[t].date() < self.df.index[bar].date() and self.trades.position.iloc[t] == 'short':
                    if self.df.h.iloc[bar] > self.trades.sl.iloc[t]:
                        self.trades.outcome_pips.iloc[t] = self.trades.entry_price.iloc[t] - self.trades.sl.iloc[t]
                        print("{}: Short Position from {} closed | SL: {}".format(self.df.index[bar].date(), self.trades.index[t].date(), self.trades.sl.iloc[t]))
                    elif self.df.l.iloc[bar] < self.trades.tp.iloc[t]:
                        self.trades.outcome_pips.iloc[t] = self.trades.entry_price.iloc[t] - self.trades.tp.iloc[t]
                        print("{}: Short Position from {} closed | TP: {}".format(self.df.index[bar].date(), self.trades.index[t].date(), self.trades.tp.iloc[t]))
                    
        print("It took {} minutes to run".format(round((time.time() - start_time)/60)))
        
    def check_outcome(self, amount, risk):
        start_time = time.time() #timer

        self.trades = self.trades[self.trades['outcome_pips'] !=0] #dropping trades which were not closed
        drop_fix = [] #dropping trades if previous trade had the same entry price
        for i in range(1, len(self.trades)):
            if abs(self.trades.entry_price[i] - self.trades.entry_price[i - 1]) < (self.trades.entry_price[i]*0.0001):
                drop_fix.append(self.trades.index[i])
        self.trades.drop(drop_fix, inplace=True)
        if self.trades.outcome_pips.iloc[0] < 0:
            self.trades.total_amount_fixed.iloc[0] = amount - amount * risk
        else:
            self.trades.total_amount_fixed.iloc[0] = amount + amount * risk * self.reward

        #### Defining total outcome
        # Defining total outcome fixed for fixed strategy
        for t in range(1, len(self.trades)):
            if self.trades.outcome_pips.iloc[t] < 0:
                self.trades.total_amount_fixed.iloc[t] = self.trades.total_amount_fixed.iloc[t-1] - self.trades.total_amount_fixed.iloc[t-1] * risk
            else:
                self.trades.total_amount_fixed.iloc[t] = self.trades.total_amount_fixed.iloc[t-1] + self.trades.total_amount_fixed.iloc[t-1] * risk * self.reward

        print("It took {} to run".format(time.time() - start_time))
        return self.trades

### Generating statistics, accuracy, combined amount.

In [3]:
def close_pos():
    global trades
    print(75 * "-")
    print("+++ CLOSING FINAL POSITION +++")
    print(75 * "-")
    print("+++ Strategy: BreakoutSwingFixed +++")
    print("Instrument: {} | TimeFrame: {} | RiskToReward: {}/{} | Spread: {}".format(ticker, timeframe, int(risk*100), reward, spread))
    print("First trade {}".format(trades.index[0]))
    print("Last trade {}".format(trades.index[-1]))
    txns_fixed = trades.position.count()
    long_trades = trades.loc[trades.position == 'long','position'].count()
    short_trades = trades.loc[trades.position == 'short','position'].count()
    winning_longs = trades.loc[(trades['position']=='long') & (trades['outcome_pips']>0)].position.count()
    winning_shorts = trades.loc[(trades['position']=='short') & (trades['outcome_pips']>0)].position.count()
    print("Number of trades executed = {}".format(txns_fixed))
    print("Long trades executed = {}  |  {}(%) of all trades".format(long_trades, round(long_trades/txns_fixed*100,2)))
    print("Short trades executed = {}  |  {}(%) of all trades".format(short_trades, round((short_trades)/txns_fixed*100,2)))
    print("Winning trades = {}  |  {}(%) of all trades".format(winning_longs + winning_shorts, round((winning_longs + winning_shorts)/txns_fixed*100,2)))
    print("Winning long trades = {}  |  {}(%) of winning trades  |  {}(%) of long trades".format(winning_longs, round(winning_longs/(winning_longs + winning_shorts)*100,2), round(winning_longs/(long_trades)*100,2)))
    print("Winning short trades = {}  |  {}(%) of winning trades  |  {}(%) of short trades".format(winning_shorts, round(winning_shorts/(winning_longs + winning_shorts)*100,2), round(winning_shorts/(short_trades)*100,2)))
    print(25*"+")
    perf = (trades.total_amount_fixed[-1] - amount) / amount * 100
    print("Total Performance of Strategy = {}(%)".format(round(perf, 2)))
    time_traded = int((trades.index[-1] - trades.index[0])/np.timedelta64(1,'D'))/30
    print("Monthly Projection of Performance = {}(%)".format(round(perf/time_traded, 2)))
    print(75 * "-")
    #Create dataframe with testing outcome
    wynik = pd.DataFrame([[ticker,timeframe,reward,spread,txns_fixed,long_trades,short_trades,
                           winning_longs+winning_shorts,winning_longs,winning_shorts,
                           round((winning_longs+winning_shorts)*100/txns_fixed, 2),round(perf, 2),round(perf/time_traded, 2)]],
                         columns = ['asset','timeframe','RR','spread','trades','long_trades','short_trades',
                                    'win_trades','win_longs','win_shorts','Win(%)','Perf(%)','M_Perf(%)'])
    return wynik

# Import prepared dictionary which contains average spreads for all assets
with open('Data\spreads.json', 'r') as fp:
    spreads = json.load(fp)
spreads

# Prepare dataframe to save all outcomes
strategies = pd.DataFrame(columns = ['asset','timeframe','RR','spread','trades','long_trades','short_trades',
                                    'win_trades','win_longs','win_shorts','Win(%)','Perf(%)','M_Perf(%)'])

In [4]:
# Specify size of trading account and risk % wide taken on each trade
# risk to reward ratio is fixed as 3 to 1
amount = 10000
risk = 0.01
reward = 3
timeframe = "M3" # it can be changed to M3

In [5]:
instruments = api.get_instruments()
instruments_list = []
for i in instruments:
    instruments_list.append(i[1])
instruments_list

['AUD_CAD',
 'AUD_CHF',
 'AUD_HKD',
 'AUD_JPY',
 'AUD_NZD',
 'AUD_SGD',
 'AUD_USD',
 'AU200_AUD',
 'BCO_USD',
 'DE10YB_EUR',
 'CAD_CHF',
 'CAD_HKD',
 'CAD_JPY',
 'CAD_SGD',
 'CHF_HKD',
 'CHF_JPY',
 'CHF_ZAR',
 'CN50_USD',
 'XCU_USD',
 'CORN_USD',
 'EUR_AUD',
 'EUR_CAD',
 'EUR_CHF',
 'EUR_CZK',
 'EUR_DKK',
 'EUR_GBP',
 'EUR_HKD',
 'EUR_HUF',
 'EUR_JPY',
 'EUR_NOK',
 'EUR_NZD',
 'EUR_PLN',
 'EUR_SEK',
 'EUR_SGD',
 'EUR_TRY',
 'EUR_USD',
 'EUR_ZAR',
 'EU50_EUR',
 'FR40_EUR',
 'GBP_AUD',
 'GBP_CAD',
 'GBP_CHF',
 'GBP_HKD',
 'GBP_JPY',
 'GBP_NZD',
 'GBP_PLN',
 'GBP_SGD',
 'GBP_USD',
 'GBP_ZAR',
 'DE30_EUR',
 'XAU_USD',
 'XAU_AUD',
 'XAU_CAD',
 'XAU_CHF',
 'XAU_EUR',
 'XAU_GBP',
 'XAU_HKD',
 'XAU_JPY',
 'XAU_NZD',
 'XAU_SGD',
 'XAU_XAG',
 'HKD_JPY',
 'HK33_HKD',
 'IN50_USD',
 'JP225_USD',
 'NZD_CAD',
 'NZD_CHF',
 'NZD_HKD',
 'NZD_JPY',
 'NZD_SGD',
 'NZD_USD',
 'NATGAS_USD',
 'NL25_EUR',
 'XPD_USD',
 'XPT_USD',
 'SGD_CHF',
 'SGD_JPY',
 'XAG_USD',
 'XAG_AUD',
 'XAG_CAD',
 'XAG_CHF',
 'XAG_EUR'

In [8]:
len(instruments_list)

122

In [18]:
tickers = []

In [22]:
for ticker in tickers:
    data = pd.read_csv("Data/{}_{}_full.csv".format(ticker, timeframe), parse_dates = ["time"], index_col = "time")
    spread = spreads[ticker]
    BS = breakout_swing(reward, spread)
    BS.check_strategy()
    trades = BS.check_outcome(amount, risk)
    outcome = close_pos()
    strategies = strategies.append(outcome)
    trades.to_csv('Wyniki\BS_Fixed\{}_{}_RR{}_trades.csv'.format(ticker,timeframe,reward),index=True)
strategies.to_csv('Wyniki\BS_Fixed\performances.csv', index=False)

2020-01-03: BS_fixed | Go Long  | Price: 8767.87737 | SL: 8736.92263 | TP: 8860.74159
2020-01-03: BS_fixed | Go Long  | Price: 8768.17737 | SL: 8748.92263 | TP: 8825.94159
2020-01-03: BS_fixed | Go Long  | Price: 8791.37737 | SL: 8751.22263 | TP: 8911.84159
2020-01-03: BS_fixed | Go Long  | Price: 8818.17737 | SL: 8786.92263 | TP: 8911.94159
2020-01-03: BS_fixed | Go Long  | Price: 8821.67737 | SL: 8787.42263 | TP: 8924.44159
2020-01-03: BS_fixed | Go Long  | Price: 8821.67737 | SL: 8787.42263 | TP: 8924.44159
2020-01-03: BS_fixed | Go Long  | Price: 8837.67737 | SL: 8787.42263 | TP: 8988.44159
2020-01-05: Long Position from 2020-01-03 closed | SL: 8748.92263
2020-01-05: Long Position from 2020-01-03 closed | SL: 8751.22263
2020-01-05: Long Position from 2020-01-03 closed | SL: 8786.92263
2020-01-05: Long Position from 2020-01-03 closed | SL: 8787.42263
2020-01-05: Long Position from 2020-01-03 closed | SL: 8787.42263
2020-01-05: Long Position from 2020-01-03 closed | SL: 8787.42263
20

C:\Users\Sylwia\Anaconda3\lib\site-packages\pandas\core\indexing.py:205: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


2020-01-06: BS_fixed | Go Short | Price: 8807.12263 | SL: 8821.57737 | TP: 8766.71315
2020-01-06: BS_fixed | Go Short | Price: 8807.12263 | SL: 8821.57737 | TP: 8766.71315
2020-01-07: Short Position from 2020-01-06 closed | SL: 8821.57737
2020-01-07: Short Position from 2020-01-06 closed | SL: 8821.57737
2020-01-07: BS_fixed | Go Long  | Price: 8857.87737 | SL: 8844.22263 | TP: 8898.84159
2020-01-07: BS_fixed | Go Long  | Price: 8857.87737 | SL: 8835.22263 | TP: 8925.84159
2020-01-07: BS_fixed | Go Long  | Price: 8869.67737 | SL: 8835.22263 | TP: 8973.04159
2020-01-07: BS_fixed | Go Long  | Price: 8861.17737 | SL: 8826.22263 | TP: 8966.04159
2020-01-07: BS_fixed | Go Long  | Price: 8871.17737 | SL: 8826.22263 | TP: 9006.04159
2020-01-08: Long Position from 2020-01-07 closed | SL: 8844.22263
2020-01-08: Long Position from 2020-01-07 closed | SL: 8835.22263
2020-01-08: Long Position from 2020-01-07 closed | SL: 8835.22263
2020-01-08: Long Position from 2020-01-07 closed | SL: 8826.22263


2020-01-24: BS_fixed | Go Long  | Price: 9272.67737 | SL: 9264.72263 | TP: 9296.54159
2020-01-24: BS_fixed | Go Long  | Price: 9272.67737 | SL: 9264.72263 | TP: 9296.54159
2020-01-24: BS_fixed | Go Long  | Price: 9272.67737 | SL: 9264.72263 | TP: 9296.54159
2020-01-26: Long Position from 2020-01-24 closed | SL: 9249.62263
2020-01-26: Long Position from 2020-01-24 closed | SL: 9249.62263
2020-01-26: Long Position from 2020-01-24 closed | SL: 9249.62263
2020-01-26: Long Position from 2020-01-24 closed | SL: 9264.72263
2020-01-26: Long Position from 2020-01-24 closed | SL: 9264.72263
2020-01-26: Long Position from 2020-01-24 closed | SL: 9264.72263
2020-01-28: BS_fixed | Go Long  | Price: 9036.27737 | SL: 9022.32263 | TP: 9078.14159
2020-01-28: BS_fixed | Go Short | Price: 9018.32263 | SL: 9035.27737 | TP: 8970.41315
2020-01-28: BS_fixed | Go Short | Price: 9015.42263 | SL: 9035.27737 | TP: 8958.81315
2020-01-28: BS_fixed | Go Short | Price: 9015.42263 | SL: 9035.27737 | TP: 8958.81315
20

2020-02-06: BS_fixed | Go Long  | Price: 9438.77737 | SL: 9417.62263 | TP: 9502.24159
2020-02-07: Short Position from 2020-02-06 closed | SL: 9457.57737
2020-02-07: Short Position from 2020-02-06 closed | SL: 9439.77737
2020-02-07: Short Position from 2020-02-06 closed | SL: 9439.77737
2020-02-07: Short Position from 2020-02-06 closed | SL: 9439.77737
2020-02-07: Short Position from 2020-02-06 closed | SL: 9439.77737
2020-02-07: Long Position from 2020-02-06 closed | SL: 9417.62263
2020-02-07: BS_fixed | Go Long  | Price: 9415.47737 | SL: 9394.02263 | TP: 9479.84159
2020-02-07: Long Position from 2020-02-06 closed | SL: 9387.12263
2020-02-07: Long Position from 2020-02-06 closed | SL: 9387.12263
2020-02-09: Long Position from 2020-02-07 closed | SL: 9394.02263
2020-02-09: Long Position from 2020-02-06 closed | SL: 9356.82263
2020-02-09: Long Position from 2020-02-06 closed | SL: 9356.82263
2020-02-10: BS_fixed | Go Long  | Price: 9406.17737 | SL: 9388.02263 | TP: 9460.64159
2020-02-10:

...

2020-12-31: Short Position from 2020-12-30 closed | SL: 103.19027
2020-12-31: BS_fixed | Go Short | Price: 103.09773 | SL: 103.16127 | TP: 102.93565
2020-12-31: BS_fixed | Go Short | Price: 103.09773 | SL: 103.16127 | TP: 102.93565
2020-12-31: BS_fixed | Go Short | Price: 103.09773 | SL: 103.16127 | TP: 102.93565
2020-12-31: BS_fixed | Go Short | Price: 103.08273 | SL: 103.16127 | TP: 102.87565
2020-12-31: BS_fixed | Go Short | Price: 103.09873 | SL: 103.19827 | TP: 102.82865
2020-12-31: Short Position from 2020-12-30 closed | TP: 103.03365
2020-12-31: BS_fixed | Go Short | Price: 103.16873 | SL: 103.32327 | TP: 102.73365
2020-12-31: BS_fixed | Go Short | Price: 103.16873 | SL: 103.32327 | TP: 102.73365
2021-01-03: Short Position from 2020-12-31 closed | SL: 103.16127
2021-01-03: Short Position from 2020-12-31 closed | SL: 103.16127
2021-01-03: Short Position from 2020-12-31 closed | SL: 103.16127
2021-01-03: Short Position from 2020-12-31 closed | SL: 103.16127
2021-01-03: Short Posit

2021-01-13: BS_fixed | Go Short | Price: 103.92473 | SL: 104.00627 | TP: 103.70865
2021-01-13: BS_fixed | Go Short | Price: 103.81573 | SL: 103.94027 | TP: 103.47065
2021-01-13: BS_fixed | Go Long  | Price: 103.92827 | SL: 103.75473 | TP: 104.44889
2021-01-13: BS_fixed | Go Long  | Price: 103.98527 | SL: 103.75473 | TP: 104.67689
2021-01-14: Short Position from 2021-01-13 closed | SL: 103.94027
2021-01-14: Short Position from 2021-01-13 closed | SL: 104.00627
2021-01-14: Short Position from 2021-01-13 closed | SL: 104.00627
2021-01-14: BS_fixed | Go Long  | Price: 104.06327 | SL: 104.00673 | TP: 104.23289
2021-01-14: BS_fixed | Go Long  | Price: 104.02427 | SL: 103.95273 | TP: 104.23889
2021-01-14: BS_fixed | Go Long  | Price: 104.02627 | SL: 103.95873 | TP: 104.22889
2021-01-14: Long Position from 2021-01-13 closed | SL: 103.75473
2021-01-14: Long Position from 2021-01-13 closed | SL: 103.75473
2021-01-14: BS_fixed | Go Long  | Price: 103.71927 | SL: 103.61773 | TP: 104.02389
2021-01-

2021-01-26: BS_fixed | Go Short | Price: 103.61073 | SL: 103.68127 | TP: 103.42765
2021-01-27: Short Position from 2021-01-26 closed | TP: 103.62365
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.68127
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.78327
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.78327
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.78327
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.81827
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.82027
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.82027
2021-01-27: Short Position from 2021-01-26 closed | SL: 103.82027
2021-01-28: BS_fixed | Go Long  | Price: 104.30727 | SL: 104.19673 | TP: 104.63889
2021-01-28: BS_fixed | Go Long  | Price: 104.33827 | SL: 104.25273 | TP: 104.59489
2021-01-28: BS_fixed | Go Long  | Price: 104.34227 | SL: 104.26173 | TP: 104.58389
2021-01-28: BS_fixed | Go Long  | Price: 104.34227 | SL: 104.26173 | TP: 1

2021-02-09: Short Position from 2021-02-08 closed | TP: 105.29765
2021-02-09: Short Position from 2021-02-08 closed | TP: 105.08565
2021-02-09: Short Position from 2021-02-08 closed | TP: 105.08565
2021-02-09: Short Position from 2021-02-08 closed | TP: 105.02865
2021-02-09: Short Position from 2021-02-08 closed | TP: 104.95665
2021-02-09: BS_fixed | Go Short | Price: 104.61873 | SL: 104.70627 | TP: 104.38465
2021-02-09: BS_fixed | Go Short | Price: 104.61873 | SL: 104.67527 | TP: 104.47765
2021-02-09: BS_fixed | Go Short | Price: 104.61873 | SL: 104.65927 | TP: 104.52565
2021-02-09: BS_fixed | Go Short | Price: 104.58173 | SL: 104.71327 | TP: 104.21565
2021-02-09: BS_fixed | Go Short | Price: 104.58173 | SL: 104.71327 | TP: 104.21565
2021-02-09: BS_fixed | Go Short | Price: 104.54973 | SL: 104.71327 | TP: 104.08765
2021-02-10: Short Position from 2021-02-09 closed | TP: 104.52565
2021-02-10: Short Position from 2021-02-09 closed | SL: 104.67527
2021-02-10: Short Position from 2021-02-

2021-02-23: BS_fixed | Go Short | Price: 105.25873 | SL: 105.32327 | TP: 105.09365
2021-02-23: BS_fixed | Go Short | Price: 105.25873 | SL: 105.32327 | TP: 105.09365
2021-02-23: BS_fixed | Go Short | Price: 105.25873 | SL: 105.32327 | TP: 105.09365
2021-02-23: BS_fixed | Go Long  | Price: 105.21927 | SL: 105.06773 | TP: 105.67389
2021-02-23: BS_fixed | Go Long  | Price: 105.21927 | SL: 105.13973 | TP: 105.45789
2021-02-24: Short Position from 2021-02-23 closed | SL: 105.32327
2021-02-24: Short Position from 2021-02-23 closed | SL: 105.32327
2021-02-24: Short Position from 2021-02-23 closed | SL: 105.32327
2021-02-24: Long Position from 2021-02-23 closed | TP: 105.45789
2021-02-24: BS_fixed | Go Long  | Price: 105.52927 | SL: 105.44673 | TP: 105.77689
2021-02-24: BS_fixed | Go Long  | Price: 105.52927 | SL: 105.44673 | TP: 105.77689
2021-02-24: BS_fixed | Go Long  | Price: 105.52927 | SL: 105.44673 | TP: 105.77689
2021-02-24: BS_fixed | Go Long  | Price: 105.52927 | SL: 105.46773 | TP: 

In [5]:
strategies = pd.read_csv('Wyniki\BS_Fixed\performances_v3.csv')
strategies

asset timeframe  RR   spread  trades  long_trades  short_trades  \
0    AUD_CAD        M5   3  0.00023     553          290           263   
1    AUD_CHF        M5   3  0.00027     608          321           287   
2    AUD_HKD        M5   3  0.00143     629          335           294   
3    AUD_JPY        M5   3  0.01743     614          360           254   
4    AUD_NZD        M5   3  0.00029     545          270           275   
..       ...       ...  ..      ...     ...          ...           ...   
137  XAG_NZD        M3   3  0.03986    1084          551           533   
138  AUD_JPY        M3   3  0.01743     955          516           439   
139  XAU_SGD        M3   3  0.91289    1089          534           555   
140  XAG_CAD        M3   3  0.03391    1152          599           553   
141  USD_JPY        M3   3  0.01427     929          432           497   

     win_trades  win_longs  win_shorts  Win(%)  Perf(%)  M_Perf(%)  
0           123         68          55   22.24   -49.64      -3.61  
1           179         97          82   29.44   166.29      11.88  
2           187        102          85   29.73   196.02      14.00  
3           196        124          72   31.92   391.59      28.04  
4           163         81          82   29.91   166.14      11.84  
..          ...        ...         ...     ...      ...        ...  
137         333        196         137   30.72   892.72      63.92  
138         319        179         140   33.40  1984.77     141.77  
139         346        173         173   31.77  1479.90     105.96  
140         382        217         165   33.16  3390.76     241.62  
141         303        130         173   32.62  1336.52      95.47  

[142 rows x 13 columns]

In [12]:
strategies_m3 = strategies[strategies['timeframe'] == "M3"]
strategies_m5 = strategies[strategies['timeframe'] == "M5"]

In [13]:
best_m3 = strategies_m3.sort_values(by = ['Perf(%)'], ascending=False).head(10)
best_m3

asset timeframe  RR   spread  trades  long_trades  short_trades  \
124    US30_USD        M3   3  1.87774     989          535           454   
122  NAS100_USD        M3   3  1.47737     975          576           399   
126     GBP_USD        M3   3  0.00017     909          484           425   
136     BCO_USD        M3   3  0.03187     922          463           459   
128     XAU_HKD        M3   3  3.95293    1038          526           512   
133     XAU_USD        M3   3  0.43486    1057          528           529   
125  SPX500_USD        M3   3  0.38066     845          476           369   
123  US2000_USD        M3   3  0.37792     955          489           466   
140     XAG_CAD        M3   3  0.03391    1152          599           553   
129     XAU_GBP        M3   3  0.45239    1045          462           583   

     win_trades  win_longs  win_shorts  Win(%)   Perf(%)  M_Perf(%)  
124         393        229         164   39.74  27671.88    1981.28  
122         361        247         114   37.03   8900.11     635.72  
126         342        195         147   37.62   8131.64     582.22  
136         334        173         161   36.23   5161.72     369.57  
128         362        191         171   34.87   4871.26     347.12  
133         366        190         176   34.63   4712.20     336.59  
125         306        202         104   36.21   3663.23     264.18  
123         333        177         156   34.87   3529.83     253.94  
140         382        217         165   33.16   3390.76     241.62  
129         347        160         187   33.21   2457.90     177.25

In [14]:
best_m5 = strategies_m5.sort_values(by = ['Perf(%)'], ascending=False).head(10)
best_m5

asset timeframe  RR   spread  trades  long_trades  short_trades  \
97   NAS100_USD        M5   3  1.47737     643          411           232   
98   US2000_USD        M5   3  0.37792     623          318           305   
100    US30_USD        M5   3  1.87774     623          361           262   
99   SPX500_USD        M5   3  0.38066     557          320           237   
47      GBP_USD        M5   3  0.00017     594          260           334   
54      XAU_EUR        M5   3  0.50904     647          348           299   
56      XAU_HKD        M5   3  3.95293     628          329           299   
55      XAU_GBP        M5   3  0.45239     639          334           305   
58      XAU_NZD        M5   3  1.10764     683          327           356   
14      CHF_HKD        M5   3  0.00209     599          316           283   

     win_trades  win_longs  win_shorts  Win(%)  Perf(%)  M_Perf(%)  
97          244        170          74   37.95  2358.81     170.11  
98          220        129          91   35.31  1061.91      76.76  
100         220        135          85   35.31  1061.91      76.40  
99          201        126          75   36.09   962.70      69.43  
47          207        101         106   34.85   829.24      59.23  
54          219        122          97   33.85   777.44      56.20  
56          214        126          88   34.08   771.24      55.62  
55          216        112         104   33.80   744.36      53.94  
58          224        114         110   32.80   644.89      46.51  
14          201        114          87   33.56   596.77      42.83